In [0]:
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, StringType, IntegerType
from pyspark.sql.functions import *

In [0]:
df = spark.read.format("csv")\
    .option("inferSchema", "True")\
    .option("header", "true")\
    .option("sep", ",")\
    .option("escape", '"')\
    .load("/FileStore/tables/googleplaystore-1.csv")

In [0]:
df.show(2)

+--------------------+--------------+------+-------+----+--------+----+-----+--------------+--------------------+----------------+-----------+------------+
|                 App|      Category|Rating|Reviews|Size|Installs|Type|Price|Content Rating|              Genres|    Last Updated|Current Ver| Android Ver|
+--------------------+--------------+------+-------+----+--------+----+-----+--------------+--------------------+----------------+-----------+------------+
|Photo Editor & Ca...|ART_AND_DESIGN|   4.1|    159| 19M| 10,000+|Free|    0|      Everyone|        Art & Design| January 7, 2018|      1.0.0|4.0.3 and up|
| Coloring book moana|ART_AND_DESIGN|   3.9|    967| 14M|500,000+|Free|    0|      Everyone|Art & Design;Pret...|January 15, 2018|      2.0.0|4.0.3 and up|
+--------------------+--------------+------+-------+----+--------+----+-----+--------------+--------------------+----------------+-----------+------------+
only showing top 2 rows



In [0]:
df.printSchema()

root
 |-- App: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Rating: double (nullable = true)
 |-- Reviews: string (nullable = true)
 |-- Size: string (nullable = true)
 |-- Installs: string (nullable = true)
 |-- Type: string (nullable = true)
 |-- Price: string (nullable = true)
 |-- Content Rating: string (nullable = true)
 |-- Genres: string (nullable = true)
 |-- Last Updated: string (nullable = true)
 |-- Current Ver: string (nullable = true)
 |-- Android Ver: string (nullable = true)



In [0]:
df = df.dropDuplicates(subset=["App"])


In [0]:
df.count()

Out[264]: 9660

In [0]:
df = df.drop("Android Ver", "Current Ver", "Size", "Content Rating", "Last Updated", )

In [0]:
df.show(2)

+--------------------+--------+------+-------+----------+----+-----+------+
|                 App|Category|Rating|Reviews|  Installs|Type|Price|Genres|
+--------------------+--------+------+-------+----------+----+-----+------+
|"i DT" Fútbol. To...|  SPORTS|   NaN|     27|      500+|Free|    0|Sports|
|+Download 4 Insta...|  SOCIAL|   4.5|  40467|1,000,000+|Free|    0|Social|
+--------------------+--------+------+-------+----------+----+-----+------+
only showing top 2 rows



In [0]:
from pyspark.sql.functions import col, regexp_replace, regexp_extract

In [0]:
df = df.withColumn("Reviews", col("Reviews").cast(IntegerType()))\
.withColumn("Installs", regexp_replace(col("Installs"), "[^0-9]",""))\
.withColumn("Installs", col("Installs").cast(IntegerType()))\
.withColumn("Price", regexp_replace(col("Price"), "[$]", ""))\
.withColumn("Price", col("Price").cast(IntegerType()))

In [0]:
df.show(10)

+--------------------+------------------+------+-------+--------+----+-----+----------------+
|                 App|          Category|Rating|Reviews|Installs|Type|Price|          Genres|
+--------------------+------------------+------+-------+--------+----+-----+----------------+
|"i DT" Fútbol. To...|            SPORTS|   NaN|     27|     500|Free|    0|          Sports|
|+Download 4 Insta...|            SOCIAL|   4.5|  40467| 1000000|Free|    0|          Social|
|- Free Comics - C...|            COMICS|   3.5|    115|   10000|Free|    0|          Comics|
|                  .R|             TOOLS|   4.5|    259|   10000|Free|    0|           Tools|
|              /u/app|     COMMUNICATION|   4.7|    573|   10000|Free|    0|   Communication|
|              058.ba|NEWS_AND_MAGAZINES|   4.4|     27|     100|Free|    0|News & Magazines|
|      1. FC Köln App|            SPORTS|   4.6|   2019|  100000|Free|    0|          Sports|
|10 Best Foods for...|HEALTH_AND_FITNESS|   4.0|   2490|  50

In [0]:
df.createOrReplaceTempView ("apps")

In [0]:
%sql
select * from apps

App Category Rating Reviews Installs Type Price Genres "i DT" Fútbol. Todos Somos Técnicos. SPORTS NaN 27 500 Free 0 Sports +Download 4 Instagram Twitter SOCIAL 4.5 40467 1000000 Free 0 Social - Free Comics - Comic Apps COMICS 3.5 115 10000 Free 0 Comics .R TOOLS 4.5 259 10000 Free 0 Tools /u/app COMMUNICATION 4.7 573 10000 Free 0 Communication 058.ba NEWS_AND_MAGAZINES 4.4 27 100 Free 0 News & Magazines 1. FC Köln App SPORTS 4.6 2019 100000 Free 0 Sports 10 Best Foods for You HEALTH_AND_FITNESS 4.0 2490 500000 Free 0 Health & Fitness 10 Minutes a Day Times Tables FAMILY 4.1 681 100000 Free 0 Education 10 WPM Amateur ham radio CW Morse code trainer COMMUNICATION 3.5 10 100 Paid 1 Communication 10,000 Quotes DB (Premium) BOOKS_AND_REFERENCE 4.1 70 500 Paid 0 Books & Reference 100 Doors of Revenge FAMILY 4.1 105766 10000000 Free 0 Puzzle 100+ C Programs FAMILY 4.2 20 5000 Free 0 Education 100000+ Messages - DP, Status, Jokes & GIF 2018 LIFESTYLE 3.7 121 10000 Free 0 Lifestyle 101 C Programming Problems FAMILY 4.6 498 50000 Free 0 Education 104 Looking for a job - looking for a job, looking for a job, looking for a part-time job, health checkup, resume, treatment room BUSINESS 4.4 74359 1000000 Free 0 Business 11st SHOPPING 3.8 48732 10000000 Free 0 Shopping 12 Step Meditations & Sober Prayers AA NA AL-ANON LIFESTYLE 4.7 759 50000 Free 0 Lifestyle 14thStreetVet MEDICAL NaN 0 5 Free 0 Medical 17th Edition Cable Sizer BOOKS_AND_REFERENCE 4.4 47 1000 Paid 3 Books & Reference 1800 Contacts - Lens Store MEDICAL 4.7 23160 1000000 Free 0 Medical 1LINE – One Line with One Touch GAME 4.6 214878 10000000 Free 0 Board 1st Fed CI Mobile Banking FINANCE NaN 0 500 Free 0 Finance 2 Amateur ham radio CW Morse code practice keys TX COMMUNICATION 4.8 6 100 Paid 1 Communication 2-Player Co-op Zombie Shoot GAME 4.2 33 1000 Free 0 Action 20 Minuten (CH) NEWS_AND_MAGAZINES 3.5 14153 1000000 Free 0 News & Magazines 20 minutes (CH) NEWS_AND_MAGAZINES 3.7 4379 1000000 Free 0 News & Magazines 2000 AD Comics and Judge Dredd COMICS 3.7 705 50000 Free 0 Comics 2017 BN SM Sales Conference BUSINESS NaN 2 100 Free 0 Business 2017 EMRA Antibiotic Guide MEDICAL 4.4 12 1000 Paid 16 Medical 2018Emoji Keyboard 😂 Emoticons Lite -sticker&gif PERSONALIZATION 4.2 115773 10000000 Free 0 Personalization 2019 Tricks Es File Explores TOOLS 3.0 4 1000 Free 0 Tools 2048 BTS J Hope KPop Puzzle Game FAMILY 4.7 17 1000 Free 0 Puzzle 2048(AI) FAMILY 4.3 20 1000 Free 0 Casual 20WPM Amateur ham radio Koch CW Morse code trainer COMMUNICATION 4.3 12 100 Paid 1 Communication 21-Day Meditation Experience HEALTH_AND_FITNESS 4.4 11506 100000 Free 0 Health & Fitness 211:CK GAME 5.0 8 10 Paid 0 Arcade 211:CK Lite GAME 4.3 3 10 Free 0 Action 23rd QM BDE EO BUSINESS NaN 0 10 Free 0 Business 24 megapixel hd camera PHOTOGRAPHY 4.0 802 100000 Free 0 Photography 24/7 BZ Reis TRAVEL_AND_LOCAL 3.1 421 100000 Free 0 Travel & Local 25 Mins Ako ay may lobo Etc Pinoy Kid Song Offline FAMILY NaN 0 10 Free 0 Entertainment 25WPM Amateur ham radio Koch CW Morse code trainer TOOLS NaN 0 10 Paid 1 Tools 2Date Dating App, Love and matching DATING 4.4 41605 500000 Free 0 Dating 2Do - Reminders, To-do List & Notes PRODUCTIVITY 4.3 4649 100000 Free 0 Productivity 2GIS: directory & navigator TRAVEL_AND_LOCAL 4.5 768833 50000000 Free 0 Travel & Local 2RedBeans DATING 4.0 337 10000 Free 0 Dating 2ndLine - Second Phone Number COMMUNICATION 4.2 15880 1000000 Free 0 Communication 30 Day AB Challenge - Lumowell HEALTH_AND_FITNESS 4.8 793 10000 Free 0 Health & Fitness 30 Day Ab Challenge HEALTH_AND_FITNESS 4.5 1886 500000 Free 0 Health & Fitness 30 Day Ab Challenge FREE HEALTH_AND_FITNESS 4.3 48253 1000000 Free 0 Health & Fitness 30 Day Fitness Challenge - Workout at Home HEALTH_AND_FITNESS 4.8 471036 10000000 Free 0 Health & Fitness 30-Day Ab Challenge Tracker HEALTH_AND_FITNESS 3.5 224 10000 Free 0 Health & Fitness 30WPM Amateur ham radio Koch CW Morse code trainer FAMILY 5.0 1 10 Paid 1 Education 350 Diy Room Decor 

In [0]:
%sql
select app, reviews
from apps
order by reviews desc
limit 10

app reviews Facebook 78158306 WhatsApp Messenger 69119316 Instagram 66577313 Messenger – Text and Video Chat for Free 56642847 Clash of Clans 44891723 Clean Master- Space Cleaner & Antivirus 42916526 Subway Surfers 27722264 YouTube 25655305 Security Master - Antivirus, VPN, AppLock, Booster 24900999 Clash Royale 23133508

Databricks data profile. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select app, Installs 
from apps 
order by Installs desc 
limit 10

app Installs Google Chrome: Fast & Secure 1000000000 Hangouts 1000000000 Google Drive 1000000000 Facebook 1000000000 Google News 1000000000 Google Play Games 1000000000 Google+ 1000000000 Google Play Movies & TV 1000000000 Gmail 1000000000 Google Street View 1000000000

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select type, count(type) as total_apps
from apps 
group by 1
order by 2 desc
limit 2

type total_apps Free 8902 Paid 756

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select type, sum(Installs) as total_installs
from apps 
group by 1
order by 2 desc
limit 2;

type total_installs Free 75065572646 Paid 57364881

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select category, count(category) as total_apps
from apps 
group by 1
order by 2 desc
limit 10;

category total_apps FAMILY 1832 GAME 959 TOOLS 827 BUSINESS 420 MEDICAL 395 PERSONALIZATION 376 PRODUCTIVITY 374 LIFESTYLE 369 FINANCE 345 SPORTS 325

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select category, sum(reviews) as reviews, sum(Installs) as total_installs
from apps 
group by 1
order by 3 desc
limit 10;

category reviews total_installs GAME 622298709 13878924415 COMMUNICATION 285811368 11038276251 TOOLS 229356578 8001771915 PRODUCTIVITY 55590649 5793091369 SOCIAL 227927801 5487867902 PHOTOGRAPHY 105351270 4649147655 FAMILY 143825488 4427941505 VIDEO_PLAYERS 67484568 3926902720 TRAVEL_AND_LOCAL 26819741 2894887146 NEWS_AND_MAGAZINES 23130228 2369217760

Databricks visualization. Run in Databricks to view.